In [1]:
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from scipy.optimize import minimize
import time

## 1. Define the Levy Function

The Levy function is a challenging optimization benchmark with many local minima.

$$f(x_1, x_2) = \sin^2(3\pi x_1) + (x_1-1)^2[1+\sin^2(3\pi x_2)] + (x_2-1)^2[1+\sin^2(2\pi x_2)]$$

**Global minimum**: $f(1, 1) = 0$

In [2]:
def levy_function(x):
    """
    Levy function - a difficult optimization problem with many local minima.
    
    Args:
        x: array-like of shape (2,) representing [x1, x2]
    
    Returns:
        float: function value
    """
    x1, x2 = x[0], x[1]
    term1 = np.sin(3 * np.pi * x1)**2
    term2 = (x1 - 1)**2 * (1 + np.sin(3 * np.pi * x2)**2)
    term3 = (x2 - 1)**2 * (1 + np.sin(2 * np.pi * x2)**2)
    return term1 + term2 + term3

def levy_gradient(x):
    """
    Analytical gradient of the Levy function.
    
    Args:
        x: array-like of shape (2,) representing [x1, x2]
    
    Returns:
        array: gradient [df/dx1, df/dx2]
    """
    x1, x2 = x[0], x[1]
    
    # Partial derivative with respect to x1
    dx1 = (2 * 3 * np.pi * np.sin(3 * np.pi * x1) * np.cos(3 * np.pi * x1) +
           2 * (x1 - 1) * (1 + np.sin(3 * np.pi * x2)**2))
    
    # Partial derivative with respect to x2
    dx2 = ((x1 - 1)**2 * 2 * 3 * np.pi * np.sin(3 * np.pi * x2) * np.cos(3 * np.pi * x2) +
           2 * (x2 - 1) * (1 + np.sin(2 * np.pi * x2)**2) +
           (x2 - 1)**2 * 2 * 2 * np.pi * np.sin(2 * np.pi * x2) * np.cos(2 * np.pi * x2))
    
    return np.array([dx1, dx2])

## 2. Visualize the Levy Function

In [3]:
# Create grid for visualization
x = np.linspace(-5, 5, 200)
y = np.linspace(-5, 5, 200)
X, Y = np.meshgrid(x, y)

# Calculate Z values
Z = np.zeros_like(X)
for i in range(X.shape[0]):
    for j in range(X.shape[1]):
        Z[i, j] = levy_function([X[i, j], Y[i, j]])

# Create 3D surface plot
fig_3d = go.Figure(data=[go.Surface(x=X, y=Y, z=Z, colorscale='Viridis')])
fig_3d.update_layout(
    title='Levy Function - 3D View',
    scene=dict(
        xaxis_title='x₁',
        yaxis_title='x₂',
        zaxis_title='f(x₁, x₂)'
    ),
    width=900,
    height=700
)
fig_3d.show()

In [4]:
# Create contour plot
fig_contour = go.Figure(data=[go.Contour(
    x=x, y=y, z=Z, 
    colorscale='Viridis',
    contours=dict(
        coloring='heatmap',
        showlabels=True
    )
)])

# Mark the global minimum
fig_contour.add_trace(go.Scatter(
    x=[1], y=[1],
    mode='markers',
    marker=dict(size=15, color='red', symbol='star'),
    name='Global Minimum (1, 1)'
))

fig_contour.update_layout(
    title='Levy Function - Contour Plot',
    xaxis_title='x₁',
    yaxis_title='x₂',
    width=900,
    height=700
)
fig_contour.show()

## 3. Multi-Start BFGS

BFGS is a quasi-Newton method that approximates the Hessian matrix. It's efficient but can get stuck in local minima.

**Strategy**: Run BFGS from multiple random starting points and keep the best solution.

In [5]:
def multi_start_bfgs(func, gradient, bounds, n_starts=20, seed=42):
    """
    Multi-start BFGS optimization.
    
    Args:
        func: objective function to minimize
        gradient: gradient function
        bounds: tuple of (lower, upper) bounds for each dimension
        n_starts: number of random starting points
        seed: random seed for reproducibility
    
    Returns:
        dict: results including best solution, all attempts, and statistics
    """
    np.random.seed(seed)
    
    results = []
    all_paths = []
    
    start_time = time.time()
    
    for i in range(n_starts):
        # Generate random starting point
        x0 = np.random.uniform(bounds[0], bounds[1], size=2)
        
        # Store path and function values during optimization
        path = [x0.copy()]
        f_values = [func(x0)]
        
        def callback(xk):
            path.append(xk.copy())
            f_values.append(func(xk))
        
        # Run BFGS
        result = minimize(
            func, x0, 
            method='BFGS',
            jac=gradient,
            callback=callback,
            options={'maxiter': 1000}
        )
        
        results.append({
            'x0': x0,
            'x_final': result.x,
            'f_final': result.fun,
            'n_iter': result.nit,
            'success': result.success,
            'f_values': f_values
        })
        all_paths.append(np.array(path))
    
    end_time = time.time()
    
    # Find best result
    best_idx = np.argmin([r['f_final'] for r in results])
    best_result = results[best_idx]
    
    return {
        'best_solution': best_result['x_final'],
        'best_value': best_result['f_final'],
        'best_path': all_paths[best_idx],
        'all_results': results,
        'all_paths': all_paths,
        'total_time': end_time - start_time,
        'n_starts': n_starts
    }

# Run multi-start BFGS
print("Running Multi-Start BFGS...")
bfgs_results = multi_start_bfgs(
    levy_function, 
    levy_gradient,
    bounds=(-5, 5),
    n_starts=20
)

print(f"\n=== Multi-Start BFGS Results ===")
print(f"Best solution found: {bfgs_results['best_solution']}")
print(f"Best function value: {bfgs_results['best_value']:.8f}")
print(f"Total time: {bfgs_results['total_time']:.4f} seconds")
print(f"Number of starting points: {bfgs_results['n_starts']}")

# Count how many converged to global minimum (within tolerance)
tolerance = 0.01
n_global_bfgs = sum(1 for r in bfgs_results['all_results'] if r['f_final'] < tolerance)
print(f"Converged to global minimum: {n_global_bfgs}/{bfgs_results['n_starts']} ({100*n_global_bfgs/bfgs_results['n_starts']:.1f}%)")

Running Multi-Start BFGS...

=== Multi-Start BFGS Results ===
Best solution found: [0.99999997 0.9999952 ]
Best function value: 0.00000000
Total time: 0.0740 seconds
Number of starting points: 20
Converged to global minimum: 1/20 (5.0%)


## 3.1 BFGS: Histogram and Trajectories

In [7]:
# Histogram of BFGS final values
bfgs_final_values = [r['f_final'] for r in bfgs_results['all_results']]

fig_bfgs_hist = go.Figure()
fig_bfgs_hist.add_trace(go.Histogram(
    x=bfgs_final_values,
    name='BFGS',
    marker_color='red',
    nbinsx=15
))

fig_bfgs_hist.update_layout(
    title='BFGS: Histogram of Final Function Values',
    xaxis_title='Final Function Value',
    yaxis_title='Frequency',
    showlegend=True,
    height=500,
    width=800
)
fig_bfgs_hist.show()

print(f"\nBFGS Statistics:")
print(f"  Mean:   {np.mean(bfgs_final_values):.6f}")
print(f"  Median: {np.median(bfgs_final_values):.6f}")
print(f"  Std:    {np.std(bfgs_final_values):.6f}")
print(f"  Min:    {np.min(bfgs_final_values):.6f}")
print(f"  Max:    {np.max(bfgs_final_values):.6f}")


BFGS Statistics:
  Mean:   11.799304
  Median: 8.252808
  Std:    10.470440
  Min:    0.000000
  Max:    37.561233


In [8]:
# BFGS trajectories: function values vs iteration
fig_bfgs_traj = go.Figure()

# Plot all runs
for i, result in enumerate(bfgs_results['all_results']):
    f_vals = result['f_values']
    fig_bfgs_traj.add_trace(
        go.Scatter(
            x=list(range(len(f_vals))),
            y=f_vals,
            mode='lines',
            line=dict(color='red', width=1),
            opacity=0.3,
            showlegend=False,
            hovertemplate=f'Run {i+1}<br>Iteration: %{{x}}<br>f(x): %{{y:.6f}}<extra></extra>'
        )
    )

# Highlight best run
best_bfgs_idx = np.argmin(bfgs_final_values)
best_bfgs_f_vals = bfgs_results['all_results'][best_bfgs_idx]['f_values']
fig_bfgs_traj.add_trace(
    go.Scatter(
        x=list(range(len(best_bfgs_f_vals))),
        y=best_bfgs_f_vals,
        mode='lines',
        line=dict(color='darkred', width=3),
        name='Best Run'
    )
)

fig_bfgs_traj.update_layout(
    title='BFGS: Function Value vs Iteration (All Runs)',
    xaxis_title='Iteration',
    yaxis_title='Function Value (log scale)',
    yaxis_type='log',
    height=500,
    width=1000,
    showlegend=True
)
fig_bfgs_traj.show()

print(f"\nBFGS Trajectory Statistics:")
print(f"Average iterations per run: {np.mean([len(r['f_values']) for r in bfgs_results['all_results']]):.1f}")
print(f"Min iterations: {min([len(r['f_values']) for r in bfgs_results['all_results']])}")
print(f"Max iterations: {max([len(r['f_values']) for r in bfgs_results['all_results']])}")


BFGS Trajectory Statistics:
Average iterations per run: 10.1
Min iterations: 6
Max iterations: 13


## 4. Multi-Start Gradient Descent

Gradient descent is the simplest first-order optimization method. It updates using: $x_{k+1} = x_k - \alpha \nabla f(x_k)$

**Strategy**: Run gradient descent with fixed or adaptive learning rate from multiple starting points.

In [10]:
def gradient_descent(func, gradient, x0, learning_rate=0.01, max_iter=1000, tol=1e-6):
    """
    Gradient descent optimization with fixed learning rate.
    
    Args:
        func: objective function to minimize
        gradient: gradient function
        x0: starting point
        learning_rate: step size (alpha)
        max_iter: maximum iterations
        tol: convergence tolerance on gradient norm
    
    Returns:
        dict: optimization results
    """
    x_current = np.array(x0, dtype=float)
    path = [x_current.copy()]
    f_values = [func(x_current)]
    
    for i in range(max_iter):
        grad = gradient(x_current)
        
        # Check convergence
        if np.linalg.norm(grad) < tol:
            break
        
        # Update
        x_current = x_current - learning_rate * grad
        
        # Store
        path.append(x_current.copy())
        f_values.append(func(x_current))
    
    return {
        'x_final': x_current,
        'f_final': func(x_current),
        'n_iter': len(path) - 1,
        'path': np.array(path),
        'f_values': f_values,
        'converged': np.linalg.norm(gradient(x_current)) < tol
    }

def multi_start_gradient_descent(func, gradient, bounds, n_starts=20, learning_rate=0.01, seed=42):
    """
    Multi-start Gradient Descent optimization.
    
    Args:
        func: objective function to minimize
        gradient: gradient function
        bounds: tuple of (lower, upper) bounds for each dimension
        n_starts: number of random starting points
        learning_rate: step size
        seed: random seed for reproducibility
    
    Returns:
        dict: results including best solution, all attempts, and statistics
    """
    np.random.seed(seed)
    
    results = []
    all_paths = []
    
    start_time = time.time()
    
    for i in range(n_starts):
        # Generate random starting point
        x0 = np.random.uniform(bounds[0], bounds[1], size=2)
        
        # Run gradient descent
        result = gradient_descent(
            func, gradient, x0,
            learning_rate=learning_rate,
            max_iter=1000
        )
        
        results.append({
            'x0': x0,
            'x_final': result['x_final'],
            'f_final': result['f_final'],
            'n_iter': result['n_iter'],
            'converged': result['converged'],
            'f_values': result['f_values']
        })
        all_paths.append(result['path'])
    
    end_time = time.time()
    
    # Find best result
    best_idx = np.argmin([r['f_final'] for r in results])
    best_result = results[best_idx]
    
    return {
        'best_solution': best_result['x_final'],
        'best_value': best_result['f_final'],
        'best_path': all_paths[best_idx],
        'all_results': results,
        'all_paths': all_paths,
        'total_time': end_time - start_time,
        'n_starts': n_starts
    }

# Run multi-start gradient descent
print("Running Multi-Start Gradient Descent...")
gd_results = multi_start_gradient_descent(
    levy_function,
    levy_gradient,
    bounds=(-5, 5),
    n_starts=20,
    learning_rate=0.01
)

print(f"\n=== Multi-Start Gradient Descent Results ===")
print(f"Best solution found: {gd_results['best_solution']}")
print(f"Best function value: {gd_results['best_value']:.8f}")
print(f"Total time: {gd_results['total_time']:.4f} seconds")
print(f"Number of starting points: {gd_results['n_starts']}")

# Count how many converged to global minimum
n_global_gd = sum(1 for r in gd_results['all_results'] if r['f_final'] < tolerance)
print(f"Converged to global minimum: {n_global_gd}/{gd_results['n_starts']} ({100*n_global_gd/gd_results['n_starts']:.1f}%)")

Running Multi-Start Gradient Descent...

=== Multi-Start Gradient Descent Results ===
Best solution found: [1.        1.9726624]
Best function value: 0.97371160
Total time: 1.3259 seconds
Number of starting points: 20
Converged to global minimum: 0/20 (0.0%)

=== Multi-Start Gradient Descent Results ===
Best solution found: [1.        1.9726624]
Best function value: 0.97371160
Total time: 1.3259 seconds
Number of starting points: 20
Converged to global minimum: 0/20 (0.0%)


## 4.1 Gradient Descent: Histogram and Trajectories

In [11]:
# Histogram of GD final values
gd_final_values = [r['f_final'] for r in gd_results['all_results']]

fig_gd_hist = go.Figure()
fig_gd_hist.add_trace(go.Histogram(
    x=gd_final_values,
    name='Gradient Descent',
    marker_color='blue',
    nbinsx=15
))

fig_gd_hist.update_layout(
    title='Gradient Descent: Histogram of Final Function Values',
    xaxis_title='Final Function Value',
    yaxis_title='Frequency',
    showlegend=True,
    height=500,
    width=800
)
fig_gd_hist.show()

print(f"\nGradient Descent Statistics:")
print(f"  Mean:   {np.mean(gd_final_values):.6f}")
print(f"  Median: {np.median(gd_final_values):.6f}")
print(f"  Std:    {np.std(gd_final_values):.6f}")
print(f"  Min:    {np.min(gd_final_values):.6f}")
print(f"  Max:    {np.max(gd_final_values):.6f}")


Gradient Descent Statistics:
  Mean:   8.651806
  Median: 7.730309
  Std:    6.382722
  Min:    0.973712
  Max:    25.449476


In [33]:
# GD trajectories: function values vs iteration
fig_gd_traj = go.Figure()

# Plot all runs
for i, result in enumerate(gd_results['all_results']):
    f_vals = result['f_values']
    fig_gd_traj.add_trace(
        go.Scatter(
            x=list(range(len(f_vals))),
            y=f_vals,
            mode='lines',
            line=dict(color='blue', width=1),
            opacity=0.3,
            showlegend=False,
            hovertemplate=f'Run {i+1}<br>Iteration: %{{x}}<br>f(x): %{{y:.6f}}<extra></extra>'
        )
    )

# Highlight best run
best_gd_idx = np.argmin(gd_final_values)
best_gd_f_vals = gd_results['all_results'][best_gd_idx]['f_values']
fig_gd_traj.add_trace(
    go.Scatter(
        x=list(range(len(best_gd_f_vals))),
        y=best_gd_f_vals,
        mode='lines',
        line=dict(color='darkblue', width=3),
        name='Best Run'
    )
)

fig_gd_traj.update_layout(
    title='Gradient Descent: Function Value vs Iteration (All Runs)',
    xaxis_title='Iteration',
    yaxis_title='Function Value (log scale)',
    yaxis_type='log',
    height=500,
    width=1000,
    showlegend=True
)
fig_gd_traj.show()

print(f"\nGradient Descent Trajectory Statistics:")
print(f"Average iterations per run: {np.mean([len(r['f_values']) for r in gd_results['all_results']]):.1f}")
print(f"Min iterations: {min([len(r['f_values']) for r in gd_results['all_results']])}")
print(f"Max iterations: {max([len(r['f_values']) for r in gd_results['all_results']])}")


Gradient Descent Trajectory Statistics:
Average iterations per run: 861.0
Min iterations: 60
Max iterations: 1001


## 4.2 Multi-Start ADAM

ADAM (Adaptive Moment Estimation) combines the best properties of AdaGrad and RMSProp. It computes adaptive learning rates for each parameter using first moment (mean) and second moment (uncentered variance) of gradients.

**Update rules**: 
- $m_t = \beta_1 m_{t-1} + (1-\beta_1) \nabla f(x_t)$ (first moment)
- $v_t = \beta_2 v_{t-1} + (1-\beta_2) [\nabla f(x_t)]^2$ (second moment)
- $\hat{m}_t = m_t / (1-\beta_1^t)$, $\hat{v}_t = v_t / (1-\beta_2^t)$ (bias correction)
- $x_{t+1} = x_t - \alpha \hat{m}_t / (\sqrt{\hat{v}_t} + \epsilon)$

**Strategy**: Run ADAM from multiple starting points with typical hyperparameters.

In [13]:
def adam(func, gradient, x0, learning_rate=0.01, beta1=0.9, beta2=0.999, epsilon=1e-8, max_iter=1000, tol=1e-6):
    """
    ADAM (Adaptive Moment Estimation) optimization.
    
    Args:
        func: objective function to minimize
        gradient: gradient function
        x0: starting point
        learning_rate: step size (alpha)
        beta1: exponential decay rate for first moment estimates
        beta2: exponential decay rate for second moment estimates
        epsilon: small constant for numerical stability
        max_iter: maximum iterations
        tol: convergence tolerance on gradient norm
    
    Returns:
        dict: optimization results
    """
    x_current = np.array(x0, dtype=float)
    path = [x_current.copy()]
    f_values = [func(x_current)]
    
    # Initialize first and second moment vectors
    m = np.zeros_like(x_current)
    v = np.zeros_like(x_current)
    
    for t in range(1, max_iter + 1):
        grad = gradient(x_current)
        
        # Check convergence
        if np.linalg.norm(grad) < tol:
            break
        
        # Update biased first moment estimate
        m = beta1 * m + (1 - beta1) * grad
        
        # Update biased second raw moment estimate
        v = beta2 * v + (1 - beta2) * (grad ** 2)
        
        # Compute bias-corrected first moment estimate
        m_hat = m / (1 - beta1 ** t)
        
        # Compute bias-corrected second raw moment estimate
        v_hat = v / (1 - beta2 ** t)
        
        # Update parameters
        x_current = x_current - learning_rate * m_hat / (np.sqrt(v_hat) + epsilon)
        
        # Store
        path.append(x_current.copy())
        f_values.append(func(x_current))
    
    return {
        'x_final': x_current,
        'f_final': func(x_current),
        'n_iter': len(path) - 1,
        'path': np.array(path),
        'f_values': f_values,
        'converged': np.linalg.norm(gradient(x_current)) < tol
    }

def multi_start_adam(func, gradient, bounds, n_starts=20, learning_rate=0.01, seed=42):
    """
    Multi-start ADAM optimization.
    
    Args:
        func: objective function to minimize
        gradient: gradient function
        bounds: tuple of (lower, upper) bounds for each dimension
        n_starts: number of random starting points
        learning_rate: step size
        seed: random seed for reproducibility
    
    Returns:
        dict: results including best solution, all attempts, and statistics
    """
    np.random.seed(seed)
    
    results = []
    all_paths = []
    
    start_time = time.time()
    
    for i in range(n_starts):
        # Generate random starting point
        x0 = np.random.uniform(bounds[0], bounds[1], size=2)
        
        # Run ADAM
        result = adam(
            func, gradient, x0,
            learning_rate=learning_rate,
            max_iter=1000
        )
        
        results.append({
            'x0': x0,
            'x_final': result['x_final'],
            'f_final': result['f_final'],
            'n_iter': result['n_iter'],
            'converged': result['converged'],
            'f_values': result['f_values']
        })
        all_paths.append(result['path'])
    
    end_time = time.time()
    
    # Find best result
    best_idx = np.argmin([r['f_final'] for r in results])
    best_result = results[best_idx]
    
    return {
        'best_solution': best_result['x_final'],
        'best_value': best_result['f_final'],
        'best_path': all_paths[best_idx],
        'all_results': results,
        'all_paths': all_paths,
        'total_time': end_time - start_time,
        'n_starts': n_starts
    }

# Run multi-start ADAM
print("Running Multi-Start ADAM...")
adam_results = multi_start_adam(
    levy_function,
    levy_gradient,
    bounds=(-5, 5),
    n_starts=20,
    learning_rate=0.01
)

print(f"\n=== Multi-Start ADAM Results ===")
print(f"Best solution found: {adam_results['best_solution']}")
print(f"Best function value: {adam_results['best_value']:.8f}")
print(f"Total time: {adam_results['total_time']:.4f} seconds")
print(f"Number of starting points: {adam_results['n_starts']}")

# Count how many converged to global minimum
n_global_adam = sum(1 for r in adam_results['all_results'] if r['f_final'] < tolerance)
print(f"Converged to global minimum: {n_global_adam}/{adam_results['n_starts']} ({100*n_global_adam/adam_results['n_starts']:.1f}%)")

Running Multi-Start ADAM...

=== Multi-Start ADAM Results ===
Best solution found: [1.         1.97266239]
Best function value: 0.97371160
Total time: 1.0506 seconds
Number of starting points: 20
Converged to global minimum: 0/20 (0.0%)


## 4.3 ADAM: Histogram and Trajectories

In [14]:
# Histogram of ADAM final values
adam_final_values = [r['f_final'] for r in adam_results['all_results']]

fig_adam_hist = go.Figure()
fig_adam_hist.add_trace(go.Histogram(
    x=adam_final_values,
    name='ADAM',
    marker_color='green',
    nbinsx=15
))

fig_adam_hist.update_layout(
    title='ADAM: Histogram of Final Function Values',
    xaxis_title='Final Function Value',
    yaxis_title='Frequency',
    showlegend=True,
    height=500,
    width=800
)
fig_adam_hist.show()

print(f"\nADAM Statistics:")
print(f"  Mean:   {np.mean(adam_final_values):.6f}")
print(f"  Median: {np.median(adam_final_values):.6f}")
print(f"  Std:    {np.std(adam_final_values):.6f}")
print(f"  Min:    {np.min(adam_final_values):.6f}")
print(f"  Max:    {np.max(adam_final_values):.6f}")


ADAM Statistics:
  Mean:   18.416153
  Median: 20.099818
  Std:    10.087035
  Min:    0.973712
  Max:    33.881915


In [15]:
# ADAM trajectories: function values vs iteration
fig_adam_traj = go.Figure()

# Plot all runs
for i, result in enumerate(adam_results['all_results']):
    f_vals = result['f_values']
    fig_adam_traj.add_trace(
        go.Scatter(
            x=list(range(len(f_vals))),
            y=f_vals,
            mode='lines',
            line=dict(color='green', width=1),
            opacity=0.3,
            showlegend=False,
            hovertemplate=f'Run {i+1}<br>Iteration: %{{x}}<br>f(x): %{{y:.6f}}<extra></extra>'
        )
    )

# Highlight best run
best_adam_idx = np.argmin(adam_final_values)
best_adam_f_vals = adam_results['all_results'][best_adam_idx]['f_values']
fig_adam_traj.add_trace(
    go.Scatter(
        x=list(range(len(best_adam_f_vals))),
        y=best_adam_f_vals,
        mode='lines',
        line=dict(color='darkgreen', width=3),
        name='Best Run'
    )
)

fig_adam_traj.update_layout(
    title='ADAM: Function Value vs Iteration (All Runs)',
    xaxis_title='Iteration',
    yaxis_title='Function Value (log scale)',
    yaxis_type='log',
    height=500,
    width=1000,
    showlegend=True
)
fig_adam_traj.show()

print(f"\nADAM Trajectory Statistics:")
print(f"Average iterations per run: {np.mean([len(r['f_values']) for r in adam_results['all_results']]):.1f}")
print(f"Min iterations: {min([len(r['f_values']) for r in adam_results['all_results']])}")
print(f"Max iterations: {max([len(r['f_values']) for r in adam_results['all_results']])}")


ADAM Trajectory Statistics:
Average iterations per run: 380.4
Min iterations: 268
Max iterations: 910


## 5. Simulated Annealing (From Scratch)

Simulated annealing is inspired by the metallurgical process of annealing. It can escape local minima by accepting worse solutions with decreasing probability.

**Key components**:
- **Temperature schedule**: Controls exploration vs exploitation
- **Acceptance probability**: $P(\text{accept}) = e^{-\Delta E / T}$ where $\Delta E = f(x_{\text{new}}) - f(x_{\text{current}})$
- **Cooling schedule**: Temperature decreases over time

In [22]:
def simulated_annealing(func, x0, bounds, 
                       T_init=100.0, T_min=1e-3, alpha=0.95,
                       max_iter=10000, max_iter_per_temp=100,
                       step_size=0.5, seed=None):
    """
    Simulated Annealing optimization from scratch.
    
    Args:
        func: objective function to minimize
        x0: starting point
        bounds: tuple of (lower, upper) bounds
        T_init: initial temperature
        T_min: minimum temperature (stopping criterion)
        alpha: cooling rate (T_new = alpha * T_old)
        max_iter: maximum total iterations
        max_iter_per_temp: iterations per temperature level
        step_size: size of random perturbations
        seed: random seed
    
    Returns:
        dict: optimization results
    """
    if seed is not None:
        np.random.seed(seed)
    
    # Initialize
    x_current = np.array(x0, dtype=float)
    f_current = func(x_current)
    
    x_best = x_current.copy()
    f_best = f_current
    
    T = T_init
    
    # Track history
    history = {
        'x': [x_current.copy()],
        'f': [f_current],
        'T': [T],
        'accepted': [True]
    }
    
    total_iter = 0
    n_accepted = 0
    n_rejected = 0
    
    # Main loop
    while T > T_min and total_iter < max_iter:
        
        for _ in range(max_iter_per_temp):
            if total_iter >= max_iter:
                break
            
            # Generate neighbor by random perturbation
            perturbation = np.random.uniform(-step_size, step_size, size=len(x_current))
            x_new = x_current + perturbation
            
            # Apply bounds
            x_new = np.clip(x_new, bounds[0], bounds[1])
            
            # Evaluate new point
            f_new = func(x_new)
            
            # Calculate energy difference
            delta_E = f_new - f_current
            
            # Acceptance criterion
            if delta_E < 0:
                # Always accept better solutions
                accept = True
            else:
                # Accept worse solutions with probability exp(-delta_E/T)
                acceptance_prob = np.exp(-delta_E / T)
                accept = np.random.random() < acceptance_prob
            
            # Update if accepted
            if accept:
                x_current = x_new
                f_current = f_new
                n_accepted += 1
                
                # Update best solution
                if f_current < f_best:
                    x_best = x_current.copy()
                    f_best = f_current
            else:
                n_rejected += 1
            
            # Record history (sample every few iterations to save memory)
            if total_iter % 10 == 0:
                history['x'].append(x_current.copy())
                history['f'].append(f_current)
                history['T'].append(T)
                history['accepted'].append(accept)
            
            total_iter += 1
        
        # Cool down
        T *= alpha
    
    return {
        'x_best': x_best,
        'f_best': f_best,
        'x0': x0,
        'n_iterations': total_iter,
        'n_accepted': n_accepted,
        'n_rejected': n_rejected,
        'acceptance_rate': n_accepted / (n_accepted + n_rejected),
        'history': history,
        'final_temperature': T
    }

## 6. Multi-Start Simulated Annealing

In [23]:
def multi_start_simulated_annealing(func, bounds, n_starts=20, **sa_params):
    """
    Multi-start Simulated Annealing.
    
    Args:
        func: objective function
        bounds: tuple of (lower, upper) bounds
        n_starts: number of random starting points
        **sa_params: parameters for simulated_annealing function
    
    Returns:
        dict: results including best solution and all attempts
    """
    results = []
    all_histories = []
    
    start_time = time.time()
    
    for i in range(n_starts):
        # Generate random starting point
        x0 = np.random.uniform(bounds[0], bounds[1], size=2)
        
        # Run simulated annealing
        result = simulated_annealing(
            func, x0, bounds,
            seed=i,  # Different seed for each run
            **sa_params
        )
        
        results.append(result)
        all_histories.append(result['history'])
    
    end_time = time.time()
    
    # Find best result
    best_idx = np.argmin([r['f_best'] for r in results])
    best_result = results[best_idx]
    
    return {
        'best_solution': best_result['x_best'],
        'best_value': best_result['f_best'],
        'best_history': best_result['history'],
        'all_results': results,
        'all_histories': all_histories,
        'total_time': end_time - start_time,
        'n_starts': n_starts
    }

# Run multi-start simulated annealing
print("Running Multi-Start Simulated Annealing...")
sa_results = multi_start_simulated_annealing(
    levy_function,
    bounds=(-5, 5),
    n_starts=20,
    T_init=100.0,
    T_min=1e-3,
    alpha=0.95,
    max_iter=10000,
    max_iter_per_temp=100,
    step_size=0.5
)

print(f"\n=== Multi-Start Simulated Annealing Results ===")
print(f"Best solution found: {sa_results['best_solution']}")
print(f"Best function value: {sa_results['best_value']:.8f}")
print(f"Total time: {sa_results['total_time']:.4f} seconds")
print(f"Number of starting points: {sa_results['n_starts']}")

# Count how many converged to global minimum
n_global_sa = sum(1 for r in sa_results['all_results'] if r['f_best'] < tolerance)
print(f"Converged to global minimum: {n_global_sa}/{sa_results['n_starts']} ({100*n_global_sa/sa_results['n_starts']:.1f}%)")

# Average acceptance rate
avg_acceptance = np.mean([r['acceptance_rate'] for r in sa_results['all_results']])
print(f"Average acceptance rate: {avg_acceptance:.2%}")

Running Multi-Start Simulated Annealing...



=== Multi-Start Simulated Annealing Results ===
Best solution found: [1.00131417 0.99481095]
Best function value: 0.00018209
Total time: 9.8467 seconds
Number of starting points: 20
Converged to global minimum: 19/20 (95.0%)
Average acceptance rate: 82.38%


## 7. Comparison: BFGS vs GD vs ADAM vs Simulated Annealing

In [24]:
# Create comparison table
print("\n" + "="*90)
print("COMPARISON: Multi-Start BFGS vs GD vs ADAM vs Simulated Annealing")
print("="*90)
print(f"{'Metric':<35} {'BFGS':>12} {'GD':>12} {'ADAM':>12} {'SA':>12}")
print("-"*90)
print(f"{'Best function value':<35} {bfgs_results['best_value']:>12.8f} {gd_results['best_value']:>12.8f} {adam_results['best_value']:>12.8f} {sa_results['best_value']:>12.8f}")
print(f"{'Distance to true minimum':<35} {np.linalg.norm(bfgs_results['best_solution'] - [1,1]):>12.8f} {np.linalg.norm(gd_results['best_solution'] - [1,1]):>12.8f} {np.linalg.norm(adam_results['best_solution'] - [1,1]):>12.8f} {np.linalg.norm(sa_results['best_solution'] - [1,1]):>12.8f}")
print(f"{'Success rate (%)':<35} {n_global_bfgs/bfgs_results['n_starts']*100:>12.1f} {n_global_gd/gd_results['n_starts']*100:>12.1f} {n_global_adam/adam_results['n_starts']*100:>12.1f} {n_global_sa/sa_results['n_starts']*100:>12.1f}")
print(f"{'Total time (seconds)':<35} {bfgs_results['total_time']:>12.4f} {gd_results['total_time']:>12.4f} {adam_results['total_time']:>12.4f} {sa_results['total_time']:>12.4f}")
print(f"{'Time per run (seconds)':<35} {bfgs_results['total_time']/bfgs_results['n_starts']:>12.4f} {gd_results['total_time']/gd_results['n_starts']:>12.4f} {adam_results['total_time']/adam_results['n_starts']:>12.4f} {sa_results['total_time']/sa_results['n_starts']:>12.4f}")
print("="*90)


COMPARISON: Multi-Start BFGS vs GD vs ADAM vs Simulated Annealing
Metric                                      BFGS           GD         ADAM           SA
------------------------------------------------------------------------------------------
Best function value                   0.00000000   0.97371160   0.97371160   0.00018209
Distance to true minimum              0.00000480   0.97266240   0.97266239   0.00535288
Success rate (%)                             5.0          0.0          0.0         95.0
Total time (seconds)                      0.0740       1.3259       1.0506       9.8467
Time per run (seconds)                    0.0037       0.0663       0.0525       0.4923


## 8. Visualization: Optimization Paths

In [25]:
# Create contour plot with optimization paths
fig = go.Figure()

# Add contour
fig.add_trace(go.Contour(
    x=x, y=y, z=Z,
    colorscale='Viridis',
    # showscale=True,
    opacity=0.7,
    contours=dict(start=0, end=50, size=5)
))

# Add BFGS paths (show top 5)
for i, path in enumerate(bfgs_results['all_paths'][:5]):
    fig.add_trace(go.Scatter(
        x=path[:, 0], y=path[:, 1],
        mode='lines+markers',
        line=dict(color='red', width=2),
        marker=dict(size=4),
        name=f'BFGS path {i+1}',
        showlegend=(i==0),
        legendgroup='bfgs'
    ))
    # Mark starting point
    fig.add_trace(go.Scatter(
        x=[path[0, 0]], y=[path[0, 1]],
        mode='markers',
        marker=dict(size=10, color='red', symbol='circle-open'),
        showlegend=False
    ))

# Mark global minimum
fig.add_trace(go.Scatter(
    x=[1], y=[1],
    mode='markers',
    marker=dict(size=20, color='yellow', symbol='star', line=dict(width=2, color='black')),
    name='Global Minimum'
))

fig.update_layout(
    title='Multi-Start BFGS Optimization Paths on Levy Function',
    xaxis_title='x₁',
    yaxis_title='x₂',
    width=1000,
    height=800,
    showlegend=True
)
fig.show()

In [28]:
# Simulated Annealing paths
fig2 = go.Figure()

# Add contour
fig2.add_trace(go.Contour(
    x=x, y=y, z=Z,
    colorscale='Viridis',
    showscale=True,
    opacity=0.7,
    contours=dict(start=0, end=50, size=5)
))

# Add SA paths (show top 5)
for i, history in enumerate(sa_results['all_histories'][:1]):
    path = np.array(history['x'])
    fig2.add_trace(go.Scatter(
        x=path[:, 0], y=path[:, 1],
        mode='lines',
        line=dict(color='cyan', width=1),
        name=f'SA path {i+1}',
        showlegend=(i==0),
        legendgroup='sa',
        opacity=0.6
    ))
    # Mark starting point
    fig2.add_trace(go.Scatter(
        x=[path[0, 0]], y=[path[0, 1]],
        mode='markers',
        marker=dict(size=10, color='cyan', symbol='circle-open'),
        showlegend=False
    ))

# Mark global minimum
fig2.add_trace(go.Scatter(
    x=[1], y=[1],
    mode='markers',
    marker=dict(size=20, color='yellow', symbol='star', line=dict(width=2, color='black')),
    name='Global Minimum'
))

fig2.update_layout(
    title='Multi-Start Simulated Annealing Paths on Levy Function',
    xaxis_title='x₁',
    yaxis_title='x₂',
    width=1000,
    height=800,
    showlegend=True
)
fig2.show()

## 9. Convergence Analysis

In [30]:
# Plot convergence for best runs
fig_conv = make_subplots(
    rows=2, cols=2,
    subplot_titles=('BFGS Convergence', 'SA Convergence', 
                   'SA Temperature Schedule', 'SA Acceptance Pattern'),
    specs=[[{"secondary_y": False}, {"secondary_y": False}],
           [{"secondary_y": False}, {"secondary_y": False}]]
)

# BFGS convergence
best_bfgs_path = bfgs_results['best_path']
bfgs_values = [levy_function(x) for x in best_bfgs_path]
fig_conv.add_trace(
    go.Scatter(x=list(range(len(bfgs_values))), y=bfgs_values,
              mode='lines', name='BFGS', line=dict(color='red')),
    row=1, col=1
)

# SA convergence
sa_history = sa_results['best_history']
fig_conv.add_trace(
    go.Scatter(x=list(range(len(sa_history['f']))), y=sa_history['f'],
              mode='lines', name='SA', line=dict(color='cyan')),
    row=1, col=2
)

# Temperature schedule
fig_conv.add_trace(
    go.Scatter(x=list(range(len(sa_history['T']))), y=sa_history['T'],
              mode='lines', name='Temperature', line=dict(color='orange')),
    row=2, col=1
)

# Acceptance pattern (show accepted vs rejected moves)
accepted_indices = [i for i, acc in enumerate(sa_history['accepted']) if acc]
rejected_indices = [i for i, acc in enumerate(sa_history['accepted']) if not acc]
fig_conv.add_trace(
    go.Scatter(x=accepted_indices, y=[sa_history['f'][i] for i in accepted_indices],
              mode='markers', name='Accepted', marker=dict(color='green', size=3)),
    row=2, col=2
)
fig_conv.add_trace(
    go.Scatter(x=rejected_indices, y=[sa_history['f'][min(i, len(sa_history['f'])-1)] for i in rejected_indices],
              mode='markers', name='Rejected', marker=dict(color='red', size=3, opacity=0.3)),
    row=2, col=2
)

# Update axes
fig_conv.update_xaxes(title_text="Iteration", row=1, col=1)
fig_conv.update_xaxes(title_text="Iteration", row=1, col=2)
fig_conv.update_xaxes(title_text="Iteration", row=2, col=1)
fig_conv.update_xaxes(title_text="Iteration", row=2, col=2)

fig_conv.update_yaxes(title_text="Function Value", row=1, col=1)
fig_conv.update_yaxes(title_text="Function Value", row=1, col=2)
fig_conv.update_yaxes(title_text="Temperature", row=2, col=1)
fig_conv.update_yaxes(title_text="Function Value", row=2, col=2)

fig_conv.update_layout(height=800, width=1200, title_text="Convergence Analysis")
fig_conv.show()

## 10. Distribution of Final Solutions

In [31]:
# Plot distribution of final solutions
fig_dist = go.Figure()

# Add contour background
fig_dist.add_trace(go.Contour(
    x=x, y=y, z=Z,
    colorscale='Viridis',
    showscale=True,
    opacity=0.5,
    contours=dict(start=0, end=50, size=5)
))

# BFGS final solutions
bfgs_finals = np.array([r['x_final'] for r in bfgs_results['all_results']])
fig_dist.add_trace(go.Scatter(
    x=bfgs_finals[:, 0], y=bfgs_finals[:, 1],
    mode='markers',
    marker=dict(size=15, color='red', symbol='circle', 
               line=dict(width=2, color='darkred')),
    name='BFGS Final Solutions'
))

# GD final solutions
gd_finals = np.array([r['x_final'] for r in gd_results['all_results']])
fig_dist.add_trace(go.Scatter(
    x=gd_finals[:, 0], y=gd_finals[:, 1],
    mode='markers',
    marker=dict(size=15, color='blue', symbol='square',
               line=dict(width=2, color='darkblue')),
    name='GD Final Solutions'
))

# ADAM final solutions
adam_finals = np.array([r['x_final'] for r in adam_results['all_results']])
fig_dist.add_trace(go.Scatter(
    x=adam_finals[:, 0], y=adam_finals[:, 1],
    mode='markers',
    marker=dict(size=15, color='green', symbol='diamond-open',
               line=dict(width=2, color='darkgreen')),
    name='ADAM Final Solutions'
))

# SA final solutions
sa_finals = np.array([r['x_best'] for r in sa_results['all_results']])
fig_dist.add_trace(go.Scatter(
    x=sa_finals[:, 0], y=sa_finals[:, 1],
    mode='markers',
    marker=dict(size=15, color='cyan', symbol='diamond',
               line=dict(width=2, color='darkcyan')),
    name='SA Final Solutions'
))

# Global minimum
fig_dist.add_trace(go.Scatter(
    x=[1], y=[1],
    mode='markers',
    marker=dict(size=25, color='yellow', symbol='star',
               line=dict(width=3, color='black')),
    name='Global Minimum'
))

fig_dist.update_layout(
    title='Distribution of Final Solutions (20 runs each)',
    xaxis_title='x₁',
    yaxis_title='x₂',
    width=1000,
    height=800,
    showlegend=True
)
fig_dist.show()

## 11. Statistical Analysis

In [32]:
# Extract all final values
bfgs_final_values = [r['f_final'] for r in bfgs_results['all_results']]
gd_final_values = [r['f_final'] for r in gd_results['all_results']]
adam_final_values = [r['f_final'] for r in adam_results['all_results']]
sa_final_values = [r['f_best'] for r in sa_results['all_results']]

# Create box plots
fig_box = go.Figure()
fig_box.add_trace(go.Box(y=bfgs_final_values, name='BFGS', marker_color='red'))
fig_box.add_trace(go.Box(y=gd_final_values, name='Gradient Descent', marker_color='blue'))
fig_box.add_trace(go.Box(y=adam_final_values, name='ADAM', marker_color='green'))
fig_box.add_trace(go.Box(y=sa_final_values, name='Simulated Annealing', marker_color='cyan'))

fig_box.update_layout(
    title='Distribution of Final Function Values (20 runs each)',
    yaxis_title='Final Function Value',
    showlegend=True,
    height=600,
    width=800
)
fig_box.show()

# Print statistics
print("\n" + "="*60)
print("STATISTICAL SUMMARY")
print("="*60)
print(f"\nBFGS Final Values:")
print(f"  Mean:   {np.mean(bfgs_final_values):.6f}")
print(f"  Median: {np.median(bfgs_final_values):.6f}")
print(f"  Std:    {np.std(bfgs_final_values):.6f}")
print(f"  Min:    {np.min(bfgs_final_values):.6f}")
print(f"  Max:    {np.max(bfgs_final_values):.6f}")

print(f"\nGradient Descent Final Values:")
print(f"  Mean:   {np.mean(gd_final_values):.6f}")
print(f"  Median: {np.median(gd_final_values):.6f}")
print(f"  Std:    {np.std(gd_final_values):.6f}")
print(f"  Min:    {np.min(gd_final_values):.6f}")
print(f"  Max:    {np.max(gd_final_values):.6f}")

print(f"\nADAM Final Values:")
print(f"  Mean:   {np.mean(adam_final_values):.6f}")
print(f"  Median: {np.median(adam_final_values):.6f}")
print(f"  Std:    {np.std(adam_final_values):.6f}")
print(f"  Min:    {np.min(adam_final_values):.6f}")
print(f"  Max:    {np.max(adam_final_values):.6f}")

print(f"\nSimulated Annealing Final Values:")
print(f"  Mean:   {np.mean(sa_final_values):.6f}")
print(f"  Median: {np.median(sa_final_values):.6f}")
print(f"  Std:    {np.std(sa_final_values):.6f}")
print(f"  Min:    {np.min(sa_final_values):.6f}")
print(f"  Max:    {np.max(sa_final_values):.6f}")
print("="*60)


STATISTICAL SUMMARY

BFGS Final Values:
  Mean:   11.799304
  Median: 8.252808
  Std:    10.470440
  Min:    0.000000
  Max:    37.561233

Gradient Descent Final Values:
  Mean:   8.651806
  Median: 7.730309
  Std:    6.382722
  Min:    0.973712
  Max:    25.449476

ADAM Final Values:
  Mean:   18.416153
  Median: 20.099818
  Std:    10.087035
  Min:    0.973712
  Max:    33.881915

Simulated Annealing Final Values:
  Mean:   0.001936
  Median: 0.001117
  Std:    0.002305
  Min:    0.000182
  Max:    0.010099


## 10.1 Histogram of Final Function Values

In [33]:
# Create histogram of final function values
fig_hist = go.Figure()

fig_hist.add_trace(go.Histogram(
    x=bfgs_final_values,
    name='BFGS',
    marker_color='red',
    opacity=0.6,
    nbinsx=15
))

fig_hist.add_trace(go.Histogram(
    x=gd_final_values,
    name='Gradient Descent',
    marker_color='blue',
    opacity=0.5,
    nbinsx=15
))

fig_hist.add_trace(go.Histogram(
    x=adam_final_values,
    name='ADAM',
    marker_color='green',
    opacity=0.5,
    nbinsx=15
))

fig_hist.add_trace(go.Histogram(
    x=sa_final_values,
    name='Simulated Annealing',
    marker_color='cyan',
    opacity=0.5,
    nbinsx=15
))

fig_hist.update_layout(
    title='Histogram of Final Function Values (20 runs each)',
    xaxis_title='Final Function Value',
    yaxis_title='Frequency',
    barmode='overlay',
    showlegend=True,
    height=600,
adam_near_optimal = sum(1 for f in adam_final_values if f < threshold)
sa_near_optimal = sum(1 for f in sa_final_values if f < threshold)

print(f"\nNear-optimal solutions (f < {threshold}):")
print(f"BFGS: {bfgs_near_optimal}/{len(bfgs_final_values)} ({100*bfgs_near_optimal/len(bfgs_final_values):.1f}%)")
print(f"GD:   {gd_near_optimal}/{len(gd_final_values)} ({100*gd_near_optimal/len(gd_final_values):.1f}%)")

print(f"ADAM: {adam_near_optimal}/{len(adam_final_values)} ({100*adam_near_optimal/len(adam_final_values):.1f}%)")
bfgs_near_optimal = sum(1 for f in bfgs_final_values if f < threshold)print(f"SA:   {sa_near_optimal}/{len(sa_final_values)} ({100*sa_near_optimal/len(sa_final_values):.1f}%)")

print(f"SA:   {sa_near_optimal}/{len(sa_final_values)} ({100*sa_near_optimal/len(sa_final_values):.1f}%)")
gd_near_optimal = sum(1 for f in gd_final_values if f < threshold)print(f"GD:   {gd_near_optimal}/{len(gd_final_values)} ({100*gd_near_optimal/len(gd_final_values):.1f}%)")

sa_near_optimal = sum(1 for f in sa_final_values if f < threshold)print(f"BFGS: {bfgs_near_optimal}/{len(bfgs_final_values)} ({100*bfgs_near_optimal/len(bfgs_final_values):.1f}%)")

print(f"\nNear-optimal solutions (f < {threshold}):")

SyntaxError: '(' was never closed (1963949388.py, line 36)

## 10.2 Function Values vs Iteration

In [44]:
# Plot function values vs iteration for all runs
fig_traj = make_subplots(
    rows=1, cols=2,
    subplot_titles=('BFGS: Function Value vs Iteration', 'SA: Function Value vs Iteration')
)

# BFGS trajectories
for i, result in enumerate(bfgs_results['all_results']):
    f_vals = result['f_values']
    fig_traj.add_trace(
        go.Scatter(
            x=list(range(len(f_vals))),
            y=f_vals,
            mode='lines',
            line=dict(color='red', width=1),
            opacity=0.4,
            showlegend=False
        ),
        row=1, col=1
    )

# Highlight best BFGS run
best_bfgs_f_vals = bfgs_results['all_results'][np.argmin(bfgs_final_values)]['f_values']
fig_traj.add_trace(
    go.Scatter(
        x=list(range(len(best_bfgs_f_vals))),
        y=best_bfgs_f_vals,
        mode='lines',
        line=dict(color='darkred', width=3),
        name='Best BFGS'
    ),
    row=1, col=1
)

# SA trajectories
for i, result in enumerate(sa_results['all_results']):
    f_vals = result['history']['f']
    fig_traj.add_trace(
        go.Scatter(
            x=list(range(len(f_vals))),
            y=f_vals,
            mode='lines',
            line=dict(color='cyan', width=1),
            opacity=0.4,
            showlegend=False
        ),
        row=1, col=2
    )

# Highlight best SA run
best_sa_f_vals = sa_results['all_results'][np.argmin(sa_final_values)]['history']['f']
fig_traj.add_trace(
    go.Scatter(
        x=list(range(len(best_sa_f_vals))),
        y=best_sa_f_vals,
        mode='lines',
        line=dict(color='darkcyan', width=3),
        name='Best SA'
    ),
    row=1, col=2
)

# Update axes
fig_traj.update_xaxes(title_text="Iteration", row=1, col=1)
fig_traj.update_xaxes(title_text="Iteration", row=1, col=2)
fig_traj.update_yaxes(title_text="Function Value", type="log", row=1, col=1)
fig_traj.update_yaxes(title_text="Function Value", type="log", row=1, col=2)

fig_traj.update_layout(
    height=600,
    width=1400,
    title_text="Optimization Trajectories: All Runs (log scale)"
)
fig_traj.show()

print(f"\nTrajectory Statistics:")
print(f"BFGS average iterations: {np.mean([len(r['f_values']) for r in bfgs_results['all_results']]):.1f}")
print(f"SA average sampled points: {np.mean([len(r['history']['f']) for r in sa_results['all_results']]):.1f}")
print(f"SA actual iterations: {sa_results['all_results'][0]['n_iterations']} (sampled every 10)")


Trajectory Statistics:
BFGS average iterations: 10.1
SA average sampled points: 1001.0
SA actual iterations: 10000 (sampled every 10)


## 12. Key Takeaways

### BFGS Strengths:
- ✅ **Fast convergence** when starting near a minimum
- ✅ **Efficient** - uses gradient and curvature information (quasi-Newton)
- ✅ **Fewer iterations** needed
- ❌ **Gets stuck** in local minima
- ❌ **Requires gradient** (analytical or numerical)

### Gradient Descent Strengths:
- ✅ **Simple and intuitive** - easiest to implement
- ✅ **Low memory** - only needs gradient
- ✅ **Predictable behavior** with proper learning rate
- ❌ **Slower convergence** than BFGS (first-order only)
- ❌ **Gets stuck** in local minima
- ❌ **Sensitive to learning rate** choice

### Simulated Annealing Strengths:
- ✅ **Can escape local minima** through temperature-based acceptance
- ✅ **Gradient-free** - works on any function
- ✅ **More robust** to starting point
- ❌ **Slower convergence** - more iterations needed
- ❌ **Hyperparameter tuning** needed (temperature schedule)

### When to Use Each:

- **BFGS**: When function is smooth, gradient available, and you have good starting points2. Switch to BFGS for **fast local refinement**

- **Simulated Annealing**: When function has many local minima, is non-differentiable, or noisy1. Use Simulated Annealing for **global exploration**

- **Multi-Start Strategy**: Always beneficial for non-convex problems!A common strategy is to:

### Hybrid Approach:

## 13. Exercises

1. **Temperature Schedule**: Experiment with different cooling schedules (exponential, linear, logarithmic). Which works best?

2. **Step Size**: How does the step size in SA affect exploration vs exploitation?

3. **Hybrid Method**: Implement a hybrid approach that starts with SA and switches to BFGS for refinement.

4. **Different Functions**: Try these methods on:
   - Rastrigin function (highly multimodal)
   - Ackley function (many local minima)
   - Your own custom function

5. **Adaptive Step Size**: Implement adaptive step size in SA based on acceptance rate.

6. **Parallel Multi-Start**: How would you parallelize the multi-start approach?